In [93]:
!pip install -U -q transformers datasets accelerate sentencepiece
from huggingface_hub import notebook_login
notebook_login()

In [101]:
!pip install optimum[onnxruntime,exporters] onnx onnxruntime onnxoptimizer -q

In [98]:
!pip freeze | grep cupy
!pip uninstall -y cupy-cuda12x

cupy-cuda12x==12.2.0
Found existing installation: cupy-cuda12x 12.2.0
Uninstalling cupy-cuda12x-12.2.0:
  Successfully uninstalled cupy-cuda12x-12.2.0


In [2]:
from datasets import load_dataset

# If the dataset is gated/private, make sure you have run huggingface-cli login
dataset = load_dataset("BEE-spoke-data/rp_books-en", 'clean')
dataset

DatasetDict({
    train: Dataset({
        features: ['meta', 'text'],
        num_rows: 26372
    })
})

In [3]:
dataset = dataset.map(lambda x: {"first_25k": x['text'][:25000]}, num_proc=6)
dataset

DatasetDict({
    train: Dataset({
        features: ['meta', 'text', 'first_25k'],
        num_rows: 26372
    })
})

In [6]:
from optimum.pipelines import pipeline

pipe = pipeline("text-classification", model="/content/quantized_model", accelerator="ort")
question = "What's my name?"
context = "My name is Philipp and I live in Nuremberg."

pipe(context)


[{'label': 'clean', 'score': 0.9644750952720642}]

In [7]:
ds_graded = dataset.map(lambda x:
                        pipe(x['first_25k'], truncation=True)[0],
                        batched=False)

Map:   0%|          | 0/26372 [00:00<?, ? examples/s]

In [10]:
ds_graded

DatasetDict({
    train: Dataset({
        features: ['meta', 'text', 'first_25k', 'label', 'score'],
        num_rows: 26372
    })
})

In [11]:
ds_graded.remove_columns('first_25k').push_to_hub("BEE-spoke-data/rp_books-en",config_name="graded")

Uploading the dataset shards:   0%|          | 0/22 [00:00<?, ?it/s]

Creating parquet from Arrow format:   0%|          | 0/2 [00:00<?, ?ba/s]

Creating parquet from Arrow format:   0%|          | 0/2 [00:00<?, ?ba/s]

Creating parquet from Arrow format:   0%|          | 0/2 [00:00<?, ?ba/s]

Creating parquet from Arrow format:   0%|          | 0/2 [00:00<?, ?ba/s]

...

Creating parquet from Arrow format:   0%|          | 0/2 [00:00<?, ?ba/s]

Creating parquet from Arrow format:   0%|          | 0/2 [00:00<?, ?ba/s]

Creating parquet from Arrow format:   0%|          | 0/2 [00:00<?, ?ba/s]

README.md:   0%|          | 0.00/2.00k [00:00<?, ?B/s]

CommitInfo(commit_url='https://huggingface.co/datasets/BEE-spoke-data/rp_books-en/commit/19bbed6ee5a04d9d91b9f10e6276051af3b6826e', commit_message='Upload dataset', commit_description='', oid='19bbed6ee5a04d9d91b9f10e6276051af3b6826e', pr_url=None, pr_revision=None, pr_num=None)

In [15]:
df = ds_graded['train'].remove_columns(['text']).to_pandas()
df.describe()

score
count  26372.000000
mean       0.748563
std        0.136647
min        0.438285
25%        0.631447
50%        0.757510
75%        0.867193
max        0.994440

In [16]:
df.label.value_counts()

mild gibberish    21286
clean              5084
word salad            2
Name: label, dtype: int64

In [86]:
clean_ds = ds_graded.filter(lambda x: x['label']=='clean' and x['score']>= 0.6)
print(clean_ds)

mild_ds = ds_graded.filter(lambda x: x['label']=='mild gibberish' and x['score']>= 0.75)
print(mild_ds)


DatasetDict({
    train: Dataset({
        features: ['meta', 'text', 'first_25k', 'label', 'score'],
        num_rows: 2923
    })
})


Filter:   0%|          | 0/26372 [00:00<?, ? examples/s]

DatasetDict({
    train: Dataset({
        features: ['meta', 'text', 'first_25k', 'label', 'score'],
        num_rows: 12711
    })
})


In [95]:

clean_ds.remove_columns('first_25k').push_to_hub("BEE-spoke-data/rp_books-en",config_name="filtered-clean_grade")

Uploading the dataset shards:   0%|          | 0/3 [00:00<?, ?it/s]

Creating parquet from Arrow format:   0%|          | 0/1 [00:00<?, ?ba/s]

Creating parquet from Arrow format:   0%|          | 0/1 [00:00<?, ?ba/s]

Creating parquet from Arrow format:   0%|          | 0/1 [00:00<?, ?ba/s]

README.md:   0%|          | 0.00/2.50k [00:00<?, ?B/s]

CommitInfo(commit_url='https://huggingface.co/datasets/BEE-spoke-data/rp_books-en/commit/88b10d748959d25bf470c3b501ea53299c200d8c', commit_message='Upload dataset', commit_description='', oid='88b10d748959d25bf470c3b501ea53299c200d8c', pr_url=None, pr_revision=None, pr_num=None)

In [96]:
mild_ds.remove_columns('first_25k').push_to_hub("BEE-spoke-data/rp_books-en",config_name="filtered-mild_grade")

Uploading the dataset shards:   0%|          | 0/11 [00:00<?, ?it/s]

Creating parquet from Arrow format:   0%|          | 0/2 [00:00<?, ?ba/s]

Creating parquet from Arrow format:   0%|          | 0/2 [00:00<?, ?ba/s]

Creating parquet from Arrow format:   0%|          | 0/2 [00:00<?, ?ba/s]

Creating parquet from Arrow format:   0%|          | 0/2 [00:00<?, ?ba/s]

...

Creating parquet from Arrow format:   0%|          | 0/2 [00:00<?, ?ba/s]

Creating parquet from Arrow format:   0%|          | 0/2 [00:00<?, ?ba/s]

Creating parquet from Arrow format:   0%|          | 0/2 [00:00<?, ?ba/s]

README.md:   0%|          | 0.00/3.07k [00:00<?, ?B/s]

CommitInfo(commit_url='https://huggingface.co/datasets/BEE-spoke-data/rp_books-en/commit/0ad811e6954489b5329690ab93044b8dda0bf7b0', commit_message='Upload dataset', commit_description='', oid='0ad811e6954489b5329690ab93044b8dda0bf7b0', pr_url=None, pr_revision=None, pr_num=None)

In [32]:
import math

def basic_distribution_stats(numbers):
    if not numbers:
        return None

    # Calculate the mean
    mean = sum(numbers) / len(numbers)

    # Calculate the median
    sorted_numbers = sorted(numbers)
    mid = len(sorted_numbers) // 2
    median = (sorted_numbers[mid - 1] + sorted_numbers[mid]) / 2 if len(sorted_numbers) % 2 == 0 else sorted_numbers[mid]

    # Calculate the variance and standard deviation
    variance = 0
    for num in numbers:
        variance += (num - mean) ** 2
    variance /= len(numbers)
    standard_deviation = math.sqrt(variance)

    return {
        'mean': mean,
        'median': median,
        "min": min(numbers),
        "max": max(numbers),
        'variance': variance,
        'standard_deviation': standard_deviation
    }
#@markdown basic_distribution_stats
# Example usage:
numbers = [1.2, 3.4, 2.5, 5.6, 4.7]
stats = basic_distribution_stats(numbers)
print("Mean:", stats['mean'])
print("Median:", stats['median'])
print("Variance:", stats['variance'])
print("Standard Deviation:", stats['standard_deviation'])

Mean: 3.4799999999999995
Median: 3.4
Variance: 2.4295999999999998
Standard Deviation: 1.558717421471897


In [33]:
basic_distribution_stats(clean_ds['train']['score'])

{'mean': 0.642014354467392,
 'median': 0.6205157935619354,
 'min': 0.4895378053188324,
 'max': 0.9694902896881104,
 'variance': 0.010988485032607827,
 'standard_deviation': 0.10482597499001775}

In [34]:
basic_distribution_stats(mild_ds['train']['score'])


{'mean': 0.7740383158512025,
 'median': 0.7920204699039459,
 'min': 0.4629112780094147,
 'max': 0.994440495967865,
 'variance': 0.017140581955241218,
 'standard_deviation': 0.13092204533706772}

In [94]:
import random
import json
xx = random.choice(clean_ds['train'])
print(json.dumps(xx['meta'], indent=2))
print(f"score is: ", xx['score'])
print(xx['first_25k'][:1000])

{
  "publication_date": 1881,
  "short_book_title": "Harper's Young People August 2 1881 by Various",
  "url": "http://www.gutenberg.org/ebooks/48597"
}
score is:  0.6047353744506836
Produced by Annie R. McGuire

[Illustration: HARPER'S YOUNG PEOPLE]

 * * * * *

VOL. II.--NO. 92. PUBLISHED BY HARPER & BROTHERS, NEW YORK. PRICE FOUR
CENTS.

Tuesday, August 2, 1881. Copyright, 1881, by HARPER & BROTHERS. $1.50
per Year, In Advance.

 * * * * *

[Illustration: TIM SHOWS THE MARKS OF CAPTAIN BABBIGE'S WHIP.]

TIM AND TIP;

OR, THE ADVENTURES OF A BOY AND A DOG.

BY JAMES OTIS, AUTHOR OF "TOBY TYLER," ETC.

CHAPTER I.

TIM'S FLIGHT.

 "'STRAYED.--A boy from the home of the subscriber; and any one
 returning him will be suitably rewarded. Said boy is about eleven
 years old, has short light hair, a turned-up nose, and face very
 much tanned. When last seen he had on a suit of blue clothes
 considerably faded and worn, and had with him a yellow dog with a
 long body, short legs, and a short 

In [83]:
import random

xx = random.choice(mild_ds['train'])
print(xx['meta'])
print(f"score is: ", xx['score'])
print(xx['first_25k'][:2000])

{'publication_date': 1895, 'short_book_title': 'The Story of the Other Wise Man by Henry van Dyke', 'url': 'http://www.gutenberg.org/ebooks/10679'}
score is:  0.8565642833709717
E-text prepared by Margaret Macaskill, David Garcia, and the Project
Gutenberg Online Distributed Proofreading Team

THE STORY OF THE OTHER WISE MAN

BY

HENRY VAN <DW18>

[Illustration: "IT IS THE SIGN" HE SAID]

CONTENTS

INTRODUCTION

THE SIGN IN THE SKY

BY THE WATERS OF BABYLON

FOR THE SAKE OF A LITTLE CHILD

IN THE HIDDEN WAY OF SORROW

A PEARL OF GREAT PRICE

ILLUSTRATIONS

"'IT IS THE SIGN,' HE SAID"

"HE CAUGHT IT UP AND READ"

"'THERE IS NONE HERE SAVE ME"'

"HE HEALED THE SICK"

"THE OLD MAN FOLLOWED THE MULTITUDE"

"THE OTHER WISE MAN HAD FOUND THE KING"

 _Who seeks for heaven alone to save his soul,
 May keep the path, but will not reach the goal;
 While he who walks in love may wander far,
 Yet God will bring him where the blessed are._

You know the story of the Three Wise Men of the East, and 